In [1]:
import numpy as np
from time import time
#from queue import SimpleQueue as queue 
from collections import deque
from copy import deepcopy as dcopy
from collections import Counter


In [2]:
class Chessboard:
    def __init__(self,n = 4): # inicjalizacja
        self.size=n
        self.board = np.zeros((self.size),dtype=np.int)
        self.queens_counter =0 
    def position(self,row,column): # ustawienie królowej na szachownicy
        self.board[row] = column
    def print_board(self,print_full_board=True): # wyświetlenie szachownicy
        if not print_full_board:
            return
        full_chessboard = np.zeros((self.size,self.size),dtype=np.int)
        for position, queen_position in zip(range(0,self.size),self.board) :
            full_chessboard [queen_position][position] = 1
        print( full_chessboard, end='\n\n')
    def get_positions(self):
        return  self.board[:]
    def default_position(self,queens_array):
        self.board[:]  = queens_array[:]
    def add_queen_counter(self):
        self.queens_counter +=1
    def get_queen_counter(self):
        return self.queens_counter
    def set_queens_counter(self,n_queens):
        self.queens_counter = n_queens

In [3]:
def print_queens_positions(chessboard: Chessboard):
    """
    wyświetl pozycje hetmanów na szachownicy w czytelny dla człowieka sposób
    """
    print(" queens positions: {0}".format(chessboard.get_positions()+1)) # +1 dla czytelności 

In [4]:
def print_stats(n_queens,generate_counter, state_check_counter,correct_counter,timer):
    """
    wyświetl statystyki jednej iteracji eksperymentu
    """
    print("N_queens: {0}".format(n_queens))
    print("Number of correct states: {0}".format(correct_counter))
    print("Number of generated states: {0}".format(generate_counter))
    print("Number of checked states: {0}".format(state_check_counter))
    print("Time spent: {0}".format(timer), end='\n\n')

In [5]:
#test na zawarcie jednej klasy strategy
class Strategy:
    def __init__(self,size : int, Brute_Force_enabled = True, BFS_strategy=True,print_full_board=True):
        self.bf_enabled = Brute_Force_enabled #true => Brute Force | false =smart
        self.BFS_strategy =BFS_strategy#true =>BFS | false => DFS
        self.state_check_counter = 0
        self.generate_counter =0 
        self.correct_counter =0
        self.size = size
        self.q = deque()
        self.print_full_board_bool = print_full_board
        
        

    def print_opening(self):
        print('############################################################')
        if self.BFS_strategy:
            print('Breadth First Search(BFS) STRATEGY')
        else:
            print('Depth First Search(DFS) STRATEGY')
        if self.bf_enabled:
            print("Brute Force")
        else:
            print('Inteligent approach')
    def append_queue(self, state, queen_row,column_position):
        state.position(queen_row, column_position)
        self.q.append((dcopy(state.get_positions()), queen_row+1))
        self.generate_counter +=1
    def generate_primary_state(self):
        board = Chessboard(self.size)
        self.q.append((board.get_positions(),0))

    def inteligent_position(self, board,current_checked_column): 
        n_queen = board.get_queen_counter()
        board_slice = board.get_positions()[:n_queen+1]
        board_slice[n_queen] = current_checked_column
        self.state_check_counter += 1
        #drugi warunek
        counter = Counter(board_slice) 
        for values in counter.values(): 
            if values > 1: 
                return False
        for current_queen in range(0, n_queen):
            if np.abs(current_queen-n_queen) == np.abs(board_slice[current_queen]-current_checked_column):
                return False
        return True
        
        
    def generate_succesor(self,state): #queen_row => czyli jakiego hetmana będziemy ustawiać
        
        queen_row = state.get_queen_counter()
        primary_state = state.get_positions()
        if self.bf_enabled : #prymitywne podejście
            """
            Zwróć wysztkie tablice z dodanym jednym hetmanem umieszczonym w dowolnym miejscu
            """

            for column_position in range(0, self.size):
                self.append_queue(state,queen_row,column_position)
                state.default_position(primary_state)
        else: # funkcja smart
            """
            zwróc tylko poprawne wektory (bez ataków)
            """
            
            for column_position in range(0, self.size):
                    if self.inteligent_position(state,column_position):
                        self.append_queue(state,queen_row,column_position)
                        state.default_position(primary_state)       
            #print(self.q, end='\n\n')
                    
                    
        
    def check_final_board_state(self, board_state): # test osiągniecia celu
        """
        test ośiągnięcia celu
        """
        if self.bf_enabled:
            if  board_state.get_queen_counter() < self.size: # jeżeli nie umieściliśmy wszystkich hetmanów zwacamy falsz
                return False
            self.state_check_counter += 1
            #drugi warunek 
            counter = Counter(board_state.get_positions()) 
            for values in counter.values(): 
                if values > 1: 
                    return False
            #trzeci warunek
            for i,h1 in zip(range(0, self.size), board_state.get_positions()):
                for j,h2 in zip(range(0, self.size), board_state.get_positions()):
                    if i != j and np.abs(i-j) ==np.abs(h1-h2)  :
                        return False
            self.correct_counter +=1 
            return True
        else:
            if board_state.get_queen_counter() ==self.size:
                self.correct_counter +=1
                return True
            
            return False
    
    def main_loop(self):
        while len(self.q): # dopóki lista stanów do przeszukania nie jest pusta
            if self.BFS_strategy: #STRATEGIA BFS
                queens_state, n_queens = self.q.popleft() # pobierz z początku listy najstarszy stan
            else: #STRATEGIA DFS
                queens_state, n_queens = self.q.pop() # pobierz z końca listy ostatnio dodany stan
            oldest_state = Chessboard(self.size)
            
            oldest_state.default_position(queens_state)
            oldest_state.set_queens_counter(n_queens)
            if self.check_final_board_state(oldest_state): # jeżeli został osiągnięty cel
                    print_queens_positions(oldest_state) # wyświetl pierwsze znalezione rozwiązanie
                    oldest_state.print_board(self.print_full_board_bool);
                    #break
            if n_queens != self.size:
                self.generate_succesor( oldest_state) # wygeneruj wszystkich potomków aktualnego stanu
        return self.generate_counter, self.state_check_counter, self.correct_counter 
    
    

In [6]:
def Experiment(n_start=4, n_stop=20, print_full_board =1): #główna pętla eksperymentu
    if n_start <4:
        return 1# nie istnieją rozwiązania
    n_array = np.array(list(range(n_start,n_stop+1)))
    strategy_list = [True,False] #true =>BFS | false => DFS
    bf_enable_list =[True,False] #true => Brute Force | false =smart
    for n in n_array:# pętla po wielkości szachownicy 
        for strat in strategy_list:
            for bf_enabler in bf_enable_list:
                timer_start = time()
                strategy = Strategy(n,bf_enabler, strat,print_full_board)
                strategy.print_opening()
                strategy.generate_primary_state()
                generate_cnt, state_check_cnt, correct_cnt =strategy.main_loop()
                timer_stop = time()
                print_stats(n,generate_cnt, state_check_cnt,correct_cnt,timer_stop - timer_start)

In [164]:
if Experiment(4,20,print_full_board =False):
    print("error n_start must be >= 4")

############################################################
Breadth First Search(BFS) STRATEGY
Brute Force
 queens positions: [2 4 1 3]
 queens positions: [3 1 4 2]
N_queens: 4
Number of correct states: 2
Number of generated states: 340
Number of checked states: 256
Time spent: 0.03124213218688965

############################################################
Breadth First Search(BFS) STRATEGY
Inteligent approach
 queens positions: [2 4 1 3]
 queens positions: [3 1 4 2]
N_queens: 4
Number of correct states: 2
Number of generated states: 16
Number of checked states: 60
Time spent: 0.006573915481567383

############################################################
Depth First Search(DFS) STRATEGY
Brute Force
 queens positions: [3 1 4 2]
 queens positions: [2 4 1 3]
N_queens: 4
Number of correct states: 2
Number of generated states: 340
Number of checked states: 256
Time spent: 0.031264305114746094

############################################################
Depth First Search(DFS) STRATE

 queens positions: [7 5 3 1 6 4 2]
 queens positions: [7 4 1 5 2 6 3]
 queens positions: [7 3 6 2 5 1 4]
 queens positions: [7 2 4 6 1 3 5]
 queens positions: [6 4 7 1 3 5 2]
 queens positions: [6 4 2 7 5 3 1]
 queens positions: [6 3 7 4 1 5 2]
 queens positions: [6 3 5 7 1 4 2]
 queens positions: [6 3 1 4 7 5 2]
 queens positions: [6 2 5 1 4 7 3]
 queens positions: [6 1 3 5 7 2 4]
 queens positions: [5 7 2 6 3 1 4]
 queens positions: [5 7 2 4 6 1 3]
 queens positions: [5 3 1 6 4 2 7]
 queens positions: [5 2 6 3 7 4 1]
 queens positions: [5 1 6 4 2 7 3]
 queens positions: [5 1 4 7 3 6 2]
 queens positions: [4 7 5 2 6 1 3]
 queens positions: [4 7 3 6 2 5 1]
 queens positions: [4 6 1 3 5 7 2]
 queens positions: [4 2 7 5 3 1 6]
 queens positions: [4 1 5 2 6 3 7]
 queens positions: [4 1 3 6 2 7 5]
 queens positions: [3 7 4 1 5 2 6]
 queens positions: [3 7 2 4 6 1 5]
 queens positions: [3 6 2 5 1 4 7]
 queens positions: [3 5 7 2 4 6 1]
 queens positions: [3 1 6 4 2 7 5]
 queens positions: [

 queens positions: [8 4 1 3 6 2 7 5]
 queens positions: [8 3 1 6 2 5 7 4]
 queens positions: [8 2 5 3 1 7 4 6]
 queens positions: [8 2 4 1 7 5 3 6]
 queens positions: [7 5 3 1 6 8 2 4]
 queens positions: [7 4 2 8 6 1 3 5]
 queens positions: [7 4 2 5 8 1 3 6]
 queens positions: [7 3 8 2 5 1 6 4]
 queens positions: [7 3 1 6 8 5 2 4]
 queens positions: [7 2 6 3 1 4 8 5]
 queens positions: [7 2 4 1 8 5 3 6]
 queens positions: [7 1 3 8 6 4 2 5]
 queens positions: [6 8 2 4 1 7 5 3]
 queens positions: [6 4 7 1 8 2 5 3]
 queens positions: [6 4 7 1 3 5 2 8]
 queens positions: [6 4 2 8 5 7 1 3]
 queens positions: [6 4 1 5 8 2 7 3]
 queens positions: [6 3 7 4 1 8 2 5]
 queens positions: [6 3 7 2 8 5 1 4]
 queens positions: [6 3 7 2 4 8 1 5]
 queens positions: [6 3 5 8 1 4 2 7]
 queens positions: [6 3 5 7 1 4 2 8]
 queens positions: [6 3 1 8 5 2 4 7]
 queens positions: [6 3 1 8 4 2 7 5]
 queens positions: [6 3 1 7 5 8 2 4]
 queens positions: [6 2 7 1 4 8 5 3]
 queens positions: [6 2 7 1 3 5 8 4]
 

KeyboardInterrupt: 

In [12]:
def Experiment2(n_start=4, n_stop=20, print_full_board =1): #główna pętla eksperymentu
    if n_start <4:
        return 1# nie istnieją rozwiązania
    n_array = np.array(list(range(n_start,n_stop+1)))
    for n in n_array:# pętla po wielkości szachownicy 
        timer_start = time()
        strategy = Strategy(n,False, True,print_full_board)
        strategy.print_opening()
        strategy.generate_primary_state()
        generate_cnt, state_check_cnt, correct_cnt =strategy.main_loop()
        timer_stop = time()
        print_stats(n,generate_cnt, state_check_cnt,correct_cnt,timer_stop - timer_start)


In [ ]:
Experiment2(4,20,print_full_board =False)

############################################################
Breadth First Search(BFS) STRATEGY
Inteligent approach
 queens positions: [2 4 1 3]
 queens positions: [3 1 4 2]
N_queens: 4
Number of correct states: 2
Number of generated states: 16
Number of checked states: 60
Time spent: 0.014961004257202148

############################################################
Breadth First Search(BFS) STRATEGY
Inteligent approach
 queens positions: [1 3 5 2 4]
 queens positions: [1 4 2 5 3]
 queens positions: [2 4 1 3 5]
 queens positions: [2 5 3 1 4]
 queens positions: [3 1 4 2 5]
 queens positions: [3 5 2 4 1]
 queens positions: [4 1 3 5 2]
 queens positions: [4 2 5 3 1]
 queens positions: [5 2 4 1 3]
 queens positions: [5 3 1 4 2]
N_queens: 5
Number of correct states: 10
Number of generated states: 53
Number of checked states: 220
Time spent: 0.025927305221557617

############################################################
Breadth First Search(BFS) STRATEGY
Inteligent approach
 queens positi

 queens positions: [ 1  3  6  8 10  5  9  2  4  7]
 queens positions: [ 1  3  6  9  7 10  4  2  5  8]
 queens positions: [ 1  3  6  9  7 10  4  2  8  5]
 queens positions: [ 1  3  9  7 10  4  2  5  8  6]
 queens positions: [ 1  4  6  9  3 10  8  2  5  7]
 queens positions: [ 1  4  7 10  2  9  5  3  8  6]
 queens positions: [ 1  4  7 10  3  9  2  5  8  6]
 queens positions: [ 1  4  7 10  6  9  2  5  3  8]
 queens positions: [ 1  4  7 10  8  2  5  3  6  9]
 queens positions: [ 1  4  7 10  8  3  5  9  2  6]
 queens positions: [ 1  4  7 10  8  5  2  9  3  6]
 queens positions: [ 1  4  9  5  8 10  3  6  2  7]
 queens positions: [ 1  4  9  7  2 10  3  6  8  5]
 queens positions: [ 1  4  9  7 10  3  6  2  5  8]
 queens positions: [ 1  4 10  7  9  3  5  2  8  6]
 queens positions: [ 1  5  7  2 10  8  4  9  3  6]
 queens positions: [ 1  5  7 10  4  2  9  3  6  8]
 queens positions: [ 1  5  8  2  7 10  3  9  6  4]
 queens positions: [ 1  5  8 10  3  7  2  4  6  9]
 queens positions: [ 1  5  8 10

 queens positions: [ 1  3  5  7  9 11  2  4  6  8 10]
 queens positions: [ 1  3  6  9  2  8 11  4  7  5 10]
 queens positions: [ 1  3  7  9  4  2 10  6 11  5  8]
 queens positions: [ 1  3  7 10  2  9  6  4 11  8  5]
 queens positions: [ 1  3  7 10  8 11  2  4  6  9  5]
 queens positions: [ 1  3  7 11  4  8 10  5  2  6  9]
 queens positions: [ 1  3  8  6  9  2  5 11  4  7 10]
 queens positions: [ 1  3  8 10  4  9 11  5  7  2  6]
 queens positions: [ 1  3  8 11  7  2 10  6  4  9  5]
 queens positions: [ 1  3 10  7  9 11  2  4  6  8  5]
 queens positions: [ 1  3 10  8  4 11  9  6  2  5  7]
 queens positions: [ 1  4  6  9  2 10  5  3  8 11  7]
 queens positions: [ 1  4  6 10  3 11  8  5  2  9  7]
 queens positions: [ 1  4  7  9 11  2 10  6  3  5  8]
 queens positions: [ 1  4  7 10  2  5  8 11  3  6  9]
 queens positions: [ 1  4  7 11  8  3  5  9  2  6 10]
 queens positions: [ 1  4  9  3  8  2 11  6 10  7  5]
 queens positions: [ 1  4  9  7  3 10  6  2  5 11  8]
 queens positions: [ 1  4  9

 queens positions: [ 4  9  7  3 11  8  1  5 10  2  6]
 queens positions: [ 4  9  7  3 11  8  5  1  6 10  2]
 queens positions: [ 4  9 11  3  7  2  8  5  1 10  6]
 queens positions: [ 4  9 11  8  5  3  1  7 10  6  2]
 queens positions: [ 4 10  3  5  2  8 11  7  1  6  9]
 queens positions: [ 4 10  3  5  9 11  1  7  2  6  8]
 queens positions: [ 4 10  3  5  9 11  6  2  7  1  8]
 queens positions: [ 4 10  3  6  2  7 11  1  8  5  9]
 queens positions: [ 4 10  3  6 11  1  8  5  2  9  7]
 queens positions: [ 4 10  3  9  6  2 11  1  7  5  8]
 queens positions: [ 4 10  3 11  2  7  9  1  5  8  6]
 queens positions: [ 4 10  3 11  6  8  2  5  1  9  7]
 queens positions: [ 4 10  5  2  9  3  6  8  1 11  7]
 queens positions: [ 4 10  5  3  9 11  2  8  6  1  7]
 queens positions: [ 4 10  5  3 11  7  2  6  9  1  8]
 queens positions: [ 4 10  5 11  6  1  7  2  8  3  9]
 queens positions: [ 4 10  7  3  1 11  9  6  2  5  8]
 queens positions: [ 4 10  7  3  6 11  9  1  5  8  2]
 queens positions: [ 4 10  7

 queens positions: [ 6  9  2  5  1 10  7 11  3  8  4]
 queens positions: [ 6  9  2  5  7 10  1 11  4  8  3]
 queens positions: [ 6  9  2  5  8 10  1  4 11  7  3]
 queens positions: [ 6  9  2  8  1  3  7 10  4 11  5]
 queens positions: [ 6  9  2  8  5  3  1 10  7 11  4]
 queens positions: [ 6  9  2 10  3  7 11  4  1  5  8]
 queens positions: [ 6  9  2 10  8  3  1  4  7  5 11]
 queens positions: [ 6  9  3  1  7 10  2 11  5  8  4]
 queens positions: [ 6  9  3  1  8  4 11  7 10  2  5]
 queens positions: [ 6  9  3  1 11  7 10  2  5  8  4]
 queens positions: [ 6  9  3  5 11  2 10  7  1  4  8]
 queens positions: [ 6  9  3  5 11  2 10  7  4  8  1]
 queens positions: [ 6  9  3  8 11  4  1 10  5  7  2]
 queens positions: [ 6  9  3 10  4  2  8 11  1  7  5]
 queens positions: [ 6  9  3 10  7  4  1 11  8  5  2]
 queens positions: [ 6  9  3 10  7  4 11  1  8  5  2]
 queens positions: [ 6  9  5  1  4 10  7 11  3  8  2]
 queens positions: [ 6  9  5  1 11  7  2  4  8 10  3]
 queens positions: [ 6  9  5

...

 queens positions: [12  8  5  3 13 11  2  6 10  1  4  9  7]
 queens positions: [12  8  5  7  1  6  2  9 13  4 10  3 11]
 queens positions: [12  8  5  7  1  6  2 13 10  4  9 11  3]
 queens positions: [12  8  5  7  1 10  2  6  3  9 11 13  4]
 queens positions: [12  8  5  7  1 11  2  6  3  9  4 13 10]
 queens positions: [12  8  5  7  1 11  2  6 13 10  4  9  3]
 queens positions: [12  8  5  7  2 13 11  1  3 10  6  4  9]
 queens positions: [12  8  5  7  2 13 11  9  3  6  4 10  1]
 queens positions: [12  8  5  7  4  1 11 13  3  6  9  2 10]
 queens positions: [12  8  5  7 10 13 11  1  3  6  9  2  4]
 queens positions: [12  8  5 11  1  3  7 13 10  2  9  6  4]
 queens positions: [12  8  5 11  1  6 10 13  2  4  9  7  3]
 queens positions: [12  8  5 11  2  6 10  1 13  4  9  7  3]
 queens positions: [12  8  5 11  2  6 10  3 13  9  7  4  1]
 queens positions: [12  8  5 11  4  1  7 13 10  2  9  6  3]
 queens positions: [12  8  5 11  4  1 10  6 13  2  7  9  3]
 queens positions: [12  8  5 11 13  3 10

 queens positions: [12 10  8  2  5  3  1  7 11 13  6  4  9]
 queens positions: [12 10  8  2  5  3  1  9 11 13  7  4  6]
 queens positions: [12 10  8  2  5 13  1  7 11  6  3  9  4]
 queens positions: [12 10  8  3  5  2  9 11 13  7  4  6  1]
 queens positions: [12 10  8  3  5  2 11  1  6 13  9  7  4]
 queens positions: [12 10  8  3  5 13  9  1  6 11  7  2  4]
 queens positions: [12 10  8  3  5 13 11  1  7  4  6  9  2]
 queens positions: [12 10  8  3  9  2 13  1  6 11  5  7  4]
 queens positions: [12 10  8  3  9  2 13  1  7  5 11  6  4]
 queens positions: [12 10  8  3 11  2  7  1 13  5  9  6  4]
 queens positions: [12 10  8  3 11  4  1  9 13  5  7  2  6]
 queens positions: [12 10  8  4  1  3  9  7 13 11  6  2  5]
 queens positions: [12 10  8  4  1  3 11  9  7  5 13  2  6]
 queens positions: [12 10  8  4  2  9 13  6  1 11  7  5  3]
 queens positions: [12 10  8  4  2 13  9  1  5 11  6  3  7]
 queens positions: [12 10  8  4  9  1 13  2  6 11  7  5  3]
 queens positions: [12 10  8  5  1  4  9

 queens positions: [13  4 12  8  2  7  1  3  9  6 10  5 11]
 queens positions: [13  4 12  8  5  3  1  9  2  6 10  7 11]
 queens positions: [13  4 12  8  6  1  3 11  7 10  2  9  5]
 queens positions: [13  4 12  8  6  1 10  2  7  3 11  9  5]
 queens positions: [13  4 12  8  6  3  1 11  7 10  2  5  9]
 queens positions: [13  4 12  8  6  3 10  2  7  9 11  1  5]
 queens positions: [13  4 12  8  6 11  2  5  1  9  7 10  3]
 queens positions: [13  4 12  8  6 11  3  1  7 10  2  9  5]
 queens positions: [13  4 12  9  2  5  3 11  7 10  1  6  8]
 queens positions: [13  4 12  9  6  3 11  2  7 10  1  5  8]
 queens positions: [13  5  1  4  7 10 12  3  8 11  2  6  9]
 queens positions: [13  5  1  4 12 10  2  7 11  3  8  6  9]
 queens positions: [13  5  1  4 12 10  8  3 11  2  7  9  6]
 queens positions: [13  5  1  6 10 12  2  4  8  3 11  9  7]
 queens positions: [13  5  1  6 10 12  4  8  3 11  2  7  9]
 queens positions: [13  5  1  6 11  2  8 12  9  3 10  7  4]
 queens positions: [13  5  1  6 11  3  8

 queens positions: [13  7  5 11  6  1 10  2  9  3  8  4 12]
 queens positions: [13  7  5 11  6  1 10 12  3  8  2  4  9]
 queens positions: [13  7  5 11  6  4 10 12  9  2  8  1  3]
 queens positions: [13  7  5 12  1  4 11  3  8 10  2  9  6]
 queens positions: [13  7  5 12  1  6  4  2 10  3  9 11  8]
 queens positions: [13  7  5 12  2  4  8 11  3 10  6  1  9]
 queens positions: [13  7  5 12  2  4 10  3  9 11  1  8  6]
 queens positions: [13  7  5 12  2  4 11  9  3  1 10  8  6]
 queens positions: [13  7  5 12  2  6 10  3  1  8  4 11  9]
 queens positions: [13  7  5 12  2  6 10  3  1  9  4  8 11]
 queens positions: [13  7  5 12  6  1 10  4  9  3  8 11  2]
 queens positions: [13  7  9  1  3  5 10  2 11  6  4 12  8]
 queens positions: [13  7  9  1  3  5 11  2 10  6  4 12  8]
 queens positions: [13  7  9  1  3 10  6  2 12  5 11  8  4]
 queens positions: [13  7  9  1  3 10  6 11  2  5 12  8  4]
 queens positions: [13  7  9  1  5  2  8 10 12  3  6  4 11]
 queens positions: [13  7  9  1  5  2  8

 queens positions: [13 11  2  7  5  3  1 12 10  8  6  4  9]
 queens positions: [13 11  2  8  3  9  4 10  1  6 12  5  7]
 queens positions: [13 11  2  8  5  3  1 10 12  6  9  7  4]
 queens positions: [13 11  3  5  7  1 12  2  6  8 10  4  9]
 queens positions: [13 11  3  5  7  2 10 12  1  9  4  6  8]
 queens positions: [13 11  3  5  7  9  1 12  2  6  8 10  4]
 queens positions: [13 11  3  5  7  9  1 12  2  8  6  4 10]
 queens positions: [13 11  3  5  7 12 10  2  6  1  9  4  8]
 queens positions: [13 11  3  5 10  2  4 12  7  9  1  6  8]
 queens positions: [13 11  3  5 10  4  1 12  8  2  7  9  6]
 queens positions: [13 11  3  5 10  4  9 12  2  7  1  6  8]
 queens positions: [13 11  3  6  2  9  5 12 10  1  7  4  8]
 queens positions: [13 11  3  6  2 10  8  4 12  1  9  7  5]
 queens positions: [13 11  3  6  4  9  1 12 10  2  7  5  8]
 queens positions: [13 11  3  6 10  2  4 12  7  9  1  5  8]
 queens positions: [13 11  3  6 10  2  5  9 12  1  8  4  7]
 queens positions: [13 11  3  6 10  5  2